In [10]:
import os
os.environ["OMP_NUM_THREADS"] = "4" # export OMP_NUM_THREADS=4
os.environ["OPENBLAS_NUM_THREADS"] = "4" # export OPENBLAS_NUM_THREADS=4 
os.environ["MKL_NUM_THREADS"] = "4" # export MKL_NUM_THREADS=6
os.environ["VECLIB_MAXIMUM_THREADS"] = "4" # export VECLIB_MAXIMUM_THREADS=4
os.environ["NUMEXPR_NUM_THREADS"] = "4" # export NUMEXPR_NUM_THREADS=6

In [11]:
import numpy as np
from scipy.linalg import eigh
#import matplotlib.pyplot as plt
import sisl
import warnings
from grogu.useful import *

In [12]:
np.set_printoptions(linewidth=2*75)
sisl.__version__

'0.14.3'

In [13]:
# this cell mimicks an input file
fdf = sisl.get_sile('/Users/danielpozsar/Downloads/nojij/Fe3GeTe2/monolayer/soc/lat3_791/Fe3GeTe2.fdf')
# this information needs to be given at the input!!
scf_xcf_orientation=np.array([0,0,1])                #z
# list of reference directions for around which we calculate the derivatives
# o is the quantization axis, v and w are two axes perpendicular to it
# at this moment the user has to supply o,v,w on the input. 
# we can have some default sfor this
ref_xcf_orientations=[dict(o=np.array([1,0,0]),vw=[np.array([0,1,0]),np.array([0,0,1])]),
                      dict(o=np.array([0,1,0]),vw=[np.array([1,0,0]),np.array([0,0,1])]),
                      dict(o=np.array([0,0,1]),vw=[np.array([1,0,0]),np.array([0,1,0])]),]

# human readable definition of magnetic entities
magnetic_entities=[dict(atom=3    ,l=2),
                   dict(atom=4    ,l=2),
                   dict(atom=5    ,l=2),
                   dict(atom=[3,4],)]

# pair information
pairs=[dict(ai=0,aj=1,Ruc=np.array([0,0,0])),     # isotropic should be -82 meV
       dict(ai=0,aj=2,Ruc=np.array([0,0,0])),     # these should all be around -41.9 in the isotropic part
       dict(ai=1,aj=2,Ruc=np.array([0,0,0])),
       dict(ai=0,aj=2,Ruc=np.array([-1,0,0])),
       dict(ai=1,aj=2,Ruc=np.array([-1,0,0]))]

# Bz sampling
nk=np.array([10,10,0])

In [14]:
# digestion of the input
# read in geometry and hamiltonian
geo = fdf.read_geometry()
dh = fdf.read_hamiltonian()

uc_in_sc_idx=dh.lattice.sc_index([0,0,0])

# get indecies for orbitals of the magnetic entities
for i,d in enumerate(magnetic_entities):
    parsed = parse_magnetic_entity(dh,**d)
    magnetic_entities[i]['orbital_indeces'] = parsed
    magnetic_entities[i]['spin_box_indeces'] = blow_up_orbindx(parsed)

In [15]:
# WE WILL NOT NEED THIS!!
eigfile=sisl.io.siesta.eigSileSiesta('/Users/danielpozsar/Downloads/nojij/Fe3GeTe2/monolayer/soc/lat3_791/Fe3GeTe2.EIG')
EF=eigfile.read_fermi_level()
EF

-5.82448514

In [16]:
NO=dh.no # shorthand for number of orbitals in the unit cell
# preprocessing Hamiltonian and overlap matrix elements
h11  = dh.tocsr(dh.M11r)
h11 += dh.tocsr(dh.M11i)*1.0j
h11  = h11.toarray().reshape(NO,dh.n_s,NO).transpose(0,2,1).astype('complex128')

h22  = dh.tocsr(dh.M22r)
h22 += dh.tocsr(dh.M22i)*1.0j
h22  = h22.toarray().reshape(NO,dh.n_s,NO).transpose(0,2,1).astype('complex128')

h12  = dh.tocsr(dh.M12r)
h12 += dh.tocsr(dh.M12i)*1.0j
h12  = h12.toarray().reshape(NO,dh.n_s,NO).transpose(0,2,1).astype('complex128')

h21  = dh.tocsr(dh.M21r)
h21 += dh.tocsr(dh.M21i)*1.0j
h21  = h21.toarray().reshape(NO,dh.n_s,NO).transpose(0,2,1).astype('complex128')

sov = dh.tocsr(dh.S_idx).toarray().reshape(NO,dh.n_s,NO).transpose(0,2,1).astype('complex128')

# Reorganization of Hamiltonian and overlap matrix elements to SPIN BOX representation

U=np.vstack([np.kron(np.eye(NO,dtype=int),[1,0]),np.kron(np.eye(NO,dtype=int),[0,1])])
# This is the permutation that transforms ud1ud2 to u12d12
# That is this transforms FROM SPIN BOX to ORBITAL BOX => U

# the inverse transformation is U.T u12d12 to ud1ud2
# That is FROM ORBITAL BOX to SPIN BOX => U.T

# this is a test
# u12d12=np.array([np.kron([1,1],np.arange(NO)),np.kron([0,1],np.ones(NO))],dtype=int).T
# ud1ud2=np.array([np.kron(np.arange(NO),[1,1]),np.kron(np.ones(NO),[0,1])],dtype=int).T
# np.allclose(u12d12,U@ud1ud2)

hh,ss = \
np.array([U.T@np.block([[h11[:,:,i],h12[:,:,i]],
                        [h21[:,:,i],h22[:,:,i]]])@U for i in range(dh.lattice.nsc.prod())]),      \
np.array([U.T@np.block([[sov[:,:,i]  ,sov[:,:,i]*0],
                        [sov[:,:,i]*0,sov[:,:,i]  ]])@U for i in range(dh.lattice.nsc.prod())])


# symmetrizing Hamiltonian and overlap matrix to make them hermitian 
for i in range(dh.lattice.sc_off.shape[0]):
    j = dh.lattice.sc_index(-dh.lattice.sc_off[i])
    h1,h1d=hh[i],hh[j]
    hh[i],hh[j]=(h1+h1d.T.conj())/2,(h1d+h1.T.conj())/2
    s1,s1d=ss[i],ss[j]
    ss[i],ss[j]=(s1+s1d.T.conj())/2,(s1d+s1.T.conj())/2    

# identifying TRS and TRB parts of the Hamiltonian
TAUY = np.kron(np.eye(NO),tau_y)
hTR  = np.array([TAUY@hh[i].conj()@TAUY for i in range(dh.lattice.nsc.prod())])
hTRS = (hh+hTR)/2
hTRB = (hh-hTR)/2

# extracting the exchange field
traced=[spin_tracer(hTRB[i]) for i in range(dh.lattice.nsc.prod())]

XCF = np.array([np.array([f['x'] for f in traced]),
                np.array([f['y'] for f in traced]),
                np.array([f['z'] for f in traced])])
# Check if exchange field has scalar part
max_xcfs=abs(np.array(np.array([f['c'] for f in traced]))).max()
if  max_xcfs > 1e-12:
    warnings.warn(f"Exchange field has non negligeble scalr part. Largest value is {max_xcfs}")

In [17]:
# collecting information for all proposed rotations, this might generate a lot of  unnceessary data
# information being collected: 
# - matrices rotating the direction of the exchange field to the proposed reference direction
# - rotated xc field 
# - single commutators of the unit cell localized exchange field for the two variations perpendicular to the reference direction
# - double commutators of the unit cell localized exchange field for the two variations perpendicular to the reference direction


# Transformation matrices for rotating the exchange field
for i,orient in enumerate(ref_xcf_orientations):

    # obtain rotated exchange field    
    R=RotMa2b(scf_xcf_orientation,orient['o'])
    
    rot_XCF = np.einsum('ij,jklm->iklm',R, XCF)
    rot_H_XCF = sum([np.kron(rot_XCF[i],tau) for i,tau in enumerate([tau_x,tau_y,tau_z])])
    rot_H_XCF_uc = rot_H_XCF[uc_in_sc_idx]
    
    # obtain total Hamiltonian with the rotated exchange field
    rot_H = hTRS+rot_H_XCF
    
    # Update magnetic entities with commutator data for each 
    for mag_ent in magnetic_entities:
        mag_ent['Commutator_Data'] = []

    for u in orient['vw']:
        
        Tu = np.kron(np.eye(NO,dtype=int),tau_u(u))

        Vu1 = 1j/2*comm(rot_H_XCF_uc,Tu)
        Vu2 = 1/8*comm(comm(Tu,rot_H_XCF_uc),Tu)

        for mag_ent in magnetic_entities:
            idx = mag_ent['spin_box_indeces']
            mag_ent['Commutator_Data'].append(dict(Vu1=Vu1[idx,:][:,idx],
                                                   Vu2=Vu2[idx,:][:,idx]))


# TODO STORE ABOVE INFO!!!!!

In [18]:
k  = np.array([0.11441,0.234432,0.0])



In [19]:
#This goes inside the for loop for k 
k  = np.array([0,0.1,0.0])


phases = np.exp(-2j*np.pi*k@dh.lattice.sc_off.T)

np.exp(-1j * np.dot(np.dot(np.dot(dh.rcell, k), dh.cell),dh.lattice.sc_off.T))
ss.shape,rot_H_XCF.shape,hTRS.shape,phases.shape

HK=np.einsum('abc,a->bc',hTRS+rot_H_XCF,phases)
SK=np.einsum('abc,a->bc',ss,phases)

vals,vecs=eigh(HK,SK)

#This goes inside the for loop for ze
ze = -.1+0.000j
GK=vecs@np.diag(1/(ze-vals))@vecs.conj().T

#phase=np.exp(1j*np.dot(np.dot(k,dh.rcell),offset))
Gii=GK[magn_ent_idices[ai],:][:,magn_ent_idices[ai]]
Gjj=GK[magn_ent_idices[ai],:][:,magn_ent_idices[ai]]
Gij=GK[magn_ent_idices[ai],:][:,magn_ent_idices[ai]]*np.exp(-k@offset*2*np.pi)
Gji=GK[magn_ent_idices[ai],:][:,magn_ent_idices[ai]]*np.exp( k@offset*2*np.pi)

NameError: name 'magn_ent_idices' is not defined

In [ ]:
np.allclose(np.linalg.inv(ze*SK-HK),GK), abs(np.linalg.inv(ze*SK-HK)-GK).max()

In [ ]:
def hsk(dh,k=(0,0,0)):
    '''
    One way to speed up Hk and Sk generation
    '''
    k = np.asarray(k, np.float64) # this two conversion lines
    k.shape = (-1,)               # are from the sisl source

    # this generates the list of phases
    phases = np.exp(-1j * np.dot(np.dot(np.dot(dh.rcell, k), dh.cell),
                                 dh.lattice.sc_off.T))

    HK11 = np.einsum('abc,c->ab',dh.h11,phases)
    HK12 = np.einsum('abc,c->ab',dh.h12,phases)
    HK21 = np.einsum('abc,c->ab',dh.h21,phases)
    HK22 = np.einsum('abc,c->ab',dh.h22,phases)

    SK  = np.einsum('abc,c->ab',dh.sov,phases)

    return HK11,HK12,HK21,HK22,SK


In [ ]:
    

rot_xcf_mats=[]
for i,rot in enumerate(rots):
    R=RotM(*rot)             # rotation matrix to go from scf to reference direction
    R@scf_xcf_orientation    # exchange field orientation 


rot_xcf_mats = [RotM(*rot) for rot in rots] 
# directions to ratate around 
dirs_xcf = [R@scf_xcf_orientation for R in rot_xcf_mats]
dirs_deriv=[]
for o in dirs_xcf:
    x,y,z = np.eye(3)
    R = RotMa2b(z,o)
    dirs_deriv.append([R@x,R@y])


# geting the exchange field part of the reference Hamiltonians for the rotated exchange field
dh.hxc_rots=[]
for mtx in rot_xcf_mats:
    rotated_xcf = np.einsum('ij,jklm->iklm',mtx, XCF)
    dh.hxc_rots.append(sum([np.kron(rotated_xcf[i],tau) 
           for i,tau in enumerate([tau_x,tau_y,tau_z]) ]))



cummutators=[]




In [ ]:
i=0

dh.hxc_rots[i][uc_in_sc_idx]

In [ ]:
dh.hTRS.shape

In [ ]:
np.kron(np.random.rand(3,3),tau_x)

In [ ]:
dh.hh

In [ ]:
# Sanity check for the exchange field orientations
xcf_test=np.array([[abs(xcfield[i].c).max(),
                    abs(xcfield[i].x).max(),
                    abs(xcfield[i].y).max(),
                    abs(xcfield[i].z).max()] for i in range(dh.lattice.nsc.prod())])
# Check how the exchange field components behave
plt.plot(np.linalg.norm(dh.lattice.sc_off,axis=1),xcf_test[:,0],'o',label='scalar')
plt.plot(np.linalg.norm(dh.lattice.sc_off,axis=1),xcf_test[:,1],'o',label='x')
plt.plot(np.linalg.norm(dh.lattice.sc_off,axis=1),xcf_test[:,2],'o',label='y')
plt.plot(np.linalg.norm(dh.lattice.sc_off,axis=1),xcf_test[:,3],'o',label='z')
plt.yscale('log')
plt.ylim(1e-22,1e1)
plt.legend()

In [ ]:
i=41
DAT=np.vstack([np.hstack([dh.h11[:,:,i]+EF*dh.sov[:,:,i],dh.h12[:,:,i]]),
               np.hstack([dh.h21[:,:,i],                 dh.h22[:,:,i]]+EF*dh.sov[:,:,i])])
dh.lattice.sc_off[i]

In [ ]:
for i,v in enumerate(dh.lattice.sc_off):
    if np.allclose(v,np.array([1,0,0])):
        print(i)

In [ ]:
plt.pcolor((U.T@DAT@U)[:6,:6].imag)
plt.colorbar()

In [ ]:
dh.h11  = dh.tocsr(dh.M11r)
dh.h11 += dh.tocsr(dh.M11i)*1.0j
dh.h11  = dh.h11.toarray().astype('complex128')
dh.h22  = dh.tocsr(dh.M22r)
dh.h22 += dh.tocsr(dh.M22i)*1.0j
dh.h22  = dh.h22.toarray().astype('complex128')

dh.h12  = dh.tocsr(dh.M12r)
dh.h12 += dh.tocsr(dh.M12i)*1.0j
dh.h12  = dh.h12.toarray().astype('complex128')
dh.h21  = dh.tocsr(dh.M21r)
dh.h21 += dh.tocsr(dh.M21i)*1.0j
dh.h21  = dh.h21.toarray().reshape(dh.no,dh.n_s,dh.no).transpose(0,2,1).astype('complex128')


In [ ]:
dh.tocsr(dh.S_idx

In [ ]:
def hsk(dh,k=(0,0,0)):
    '''
    One way to speed up Hk and Sk generation
    '''
    k = np.asarray(k, np.float64) # this two conversion lines
    k.shape = (-1,)               # are from the sisl source

    # this generates the list of phases
    phases = np.exp(-1j * np.dot(np.dot(np.dot(dh.rcell, k), dh.cell),
                                 dh.lattice.sc_off.T))

    HK11 = np.einsum('abc,c->ab',dh.h11,phases)
    HK12 = np.einsum('abc,c->ab',dh.h12,phases)
    HK21 = np.einsum('abc,c->ab',dh.h21,phases)
    HK22 = np.einsum('abc,c->ab',dh.h22,phases)

    SK  = np.einsum('abc,c->ab',dh.sov,phases)

    return HK11,HK12,HK21,HK22,SK


In [ ]:
myHk=(lambda x:np.vstack([np.hstack([x[0],x[1]]),
                          np.hstack([x[2],x[3]])]))(hsk(dh))
mySk=(lambda x:np.vstack([np.hstack([x[-1],0*x[-1]]),
                          np.hstack([0*x[-1],x[-1]])]))(hsk(dh))

myHkshift=myHk+EF*mySk

In [ ]:
H0=np.vstack( [np.hstack([dh.h11[:,:,0],dh.h12[:,:,0]]),
               np.hstack([dh.h21[:,:,0],dh.h22[:,:,0]])])

H0shifted=np.vstack( [np.hstack([dh.h11[:,:,0]+EF*dh.sov[:,:,0],dh.h12[:,:,0]]),
                      np.hstack([dh.h21[:,:,0],                 dh.h22[:,:,0]+EF*dh.sov[:,:,0]])])

In [ ]:
(U.T@H0shifted@U)[:3,:3]

In [ ]:
plt.pcolor((U.T@H0shifted@U)[:5,:5])
plt.colorbar()

In [ ]:
np.linalg.eigvalsh(myHk+EF*mySk)

In [ ]:
dh.Hk().toarray()[:3,:3]

In [ ]:
plt.matshow(np.abs(dh.Hk().toarray()-myHk))
plt.colorbar()

In [ ]:
plt.plot(np.linalg.eigvalsh(dh.Hk().toarray())-np.linalg.eigvalsh(myHk))

In [ ]:
magnetic_entities = [parse_magnetic_entity(dh,atom=[0,1],l=2),parse_magnetic_entity(dh,atom=2,l=2)]

# TODO

- Definition of magnetic entities:
    * Through simple sequence o forbitals in the unit cell
    * Through atom specification
    * Through atom and orbital specification
- Separation of TR and TRB components of the Hamiltonian, Identification of the exchange field. 
- Definition of commutator expressions, old projection matrix elements
- Efficient calculation of Green's functions
- Calculation of energy and momentum resolved derivatives
- Parallel BZ and serial energy integral